# csv des labels numériques des lycee

## Import data from api

In [1]:
#importing necessary packages
import pandas as pd
import requests
import json

# get data 
#creating the url
url = 'https://data.occitanie.education.gouv.fr/api/records/1.0/search/?dataset=fr-en-occitanie-label-numerique-lycee&q=&rows=10000&facet=annee&facet=rne&facet=departement&facet=label'
#making the request
response = requests.get(url)
#converting the response to json
data = response.json()
#appending the data to the list

#creating an empty list to store the records
records = []

#looping through the records
for record in data['records']:
  #storing the records in the list
  records.append(record['fields'])

#creating a dataframe from the json
df = pd.DataFrame(records)

## Transforming data of df

In [2]:
#transform the label to numeric
df["label"] = pd.to_numeric(df["label"])
df["annee"] = pd.to_numeric(df["annee"])

#sort annee by ascending order
df.sort_values(by="annee",inplace=True)

#create two new columns for longitude and latitude
df['latitude'] = df['position'].apply(lambda x: float(x[0]))
df['longitude'] = df['position'].apply(lambda x: float(x[1]))

# csv des résultats des lycee professionnels

## import data from api

In [3]:
# get data
#creating the url
url = 'https://data.occitanie.education.gouv.fr/api/records/1.0/search/?dataset=fr-en-indicateurs-de-resultat-des-lycees-denseignement-professionnels&q=&rows=10000&facet=etablissement&facet=UAI&facet=annee&facet=ville&facet=academie&facet=departement&facet=secteur_public_1_prive_2&facet=libelle_region_2016'
#making the request
response = requests.get(url)
#converting the response to json
data = response.json()

#creating an empty list to store the records
records = []

#looping through the records
for record in data['records']:
  #storing the records in the list
  records.append(record['fields'])

#creating a dataframe from the json
df_lycee_pro = pd.DataFrame(records)

## Nettoyage

In [4]:
# nettoyage

# Le lycee "LYCEE PROFESSIONNEL CASTELNOUVEL" a un taux de réussite brut 0
# Il a aussi un effectif_presents_total_secteurs 1, ce qui errone la visualisation (un point très écarté)
# ainsi qu'un taux_mentions_attendu_tous_secteurs Nan
# j'ai donc décidé d'enlever ce lycee
df_lycee_pro.drop(df_lycee_pro[df_lycee_pro['code_etablissement'] == "0312063Z"].index, inplace = True)


## Transform

In [5]:
# transformation

#transform the annee to numeric
df_lycee_pro["annee"] = pd.to_numeric(df_lycee_pro["annee"])
#sort annee by ascending order
df_lycee_pro.sort_values(by="annee",inplace=True)


# transform le taux brut en numerique
df_lycee_pro["taux_brut_de_reussite_total_secteurs"] = pd.to_numeric(df_lycee_pro["taux_brut_de_reussite_total_secteurs"])

# Renommage des colonnes dans df_lycee_pro des lycées professionels pour pouvoir le concatener après après les lycées générales
df_lycee_pro.rename(columns={
  'code_etablissement' : 'UAI',
  'taux_brut_de_reussite_total_secteurs' : 'taux_reussite_total',
  'va_reu_total' : 'valeur_ajoute_totale',
  'taux_reussite_attendu_france_total_secteurs' : 'taux_reussite_attendu_total'
}, inplace=True)

df_lycee_pro = df_lycee_pro[["UAI","taux_reussite_total","valeur_ajoute_totale","taux_reussite_attendu_total","annee","departement"]]


# csv des résultats des lycées d'enseignement Général et technologique

## import data from csv

In [6]:
df_lycee_gen = pd.read_csv("../data/lycee/csv/fr-en-indicateurs-de-resultat-des-lycees-denseignement-general-et-technologique.csv", sep=";")

/tmp/ipykernel_15249/2831244245.py:1: DtypeWarning: Columns (47,48,49,51,52,53,55,56,57,58,59,71,72,73,74,75,76,77,78,79,80,81,93,95,98,100,111,113,115,126,129,130,131,134,136) have mixed types. Specify dtype option on import or set low_memory=False.
  df_lycee_gen = pd.read_csv("../data/lycee/csv/fr-en-indicateurs-de-resultat-des-lycees-denseignement-general-et-technologique.csv", sep=";")


## Nettoyage

In [7]:
# nettoyage
# filtrer les données sur occitanie
df_lycee_gen = df_lycee_gen.query("Region == 'OCCITANIE'")

## Transform

In [8]:
# transformation

#RENOMMAGE
df_lycee_gen.rename(columns={
  "Annee" : "annee",
  "Taux de reussite - Toutes series" : "taux_reussite_total",
  "Valeur ajoutee du taux de reussite - Toutes series" : "valeur_ajoute_totale",
  "Taux de reussite attendu france - Toutes series" : "taux_reussite_attendu_total",
  "Departement" : "departement"
},inplace=True)


#transform the annee to numeric
df_lycee_gen["annee"] = pd.to_numeric(df_lycee_gen["annee"])
#sort annee by ascending order
df_lycee_gen.sort_values(by="annee",inplace=True)


# transform le taux brut en numerique
df_lycee_gen["taux_reussite_total"] = pd.to_numeric(df_lycee_gen["taux_reussite_total"])

df_lycee_gen = df_lycee_gen[["UAI","taux_reussite_total","valeur_ajoute_totale","taux_reussite_attendu_total","annee","departement"]]


# Concatenation des dataframe lycées professionels et lycées générals
 - csv df_lycee_pro
 - csv df_lycee_gen

In [9]:
df_lycee_all = pd.concat([df_lycee_pro,df_lycee_gen])

# Operations sur les deux csv (merge)
 - csv labels numériques lycee
 - csv résultats scolaires des lycee professionnels

In [10]:
# merge 2 dataframes on the uri (id de l'etablissement scolaire)
df_result = pd.merge(df, df_lycee_all, left_on='rne', right_on='UAI', how="inner")

In [11]:
# merge 2 dataframes but keep all the lycee that does not have label 
df_result_all = pd.merge(df,df_lycee_all, left_on='rne', right_on='UAI', how="right")

## Nettoyage df result (resultat des lycées professionels numériques)

In [12]:
#nettoyage (supression) des colonnes ou toutes les valeures sont nulles
df_result.dropna(axis=1,how='all',inplace=True)

#nettoyage (supression) des lignes ou toutes les valeures sont nulles
df_result.dropna(axis=0,how='all',inplace=True)

# L'index 1393 a une valeure ajoutée de réusiite totale = "ND"
# par contre ce lycee a un taux_reussite_total = 84
# j'ai donc décidé de rempace le "ND" par 0 (neutre) pour ce lycee et pour tous les lycee qui ont
# une valeure ajoutée de réussite totale = "ND" (non définir)
import re
reg_ex1 = r"ND"
reg_ex2 = r"\."
aNegliger = re.compile(f"{reg_ex1}|{reg_ex2}",re.I)
subst = "0"
def apply_reg(str_):
  '''Fonction pour remplacer les "ND" par 0 tout court dans une colonne
    - paramètres : 
      - str_ : la chaine de caractère dans laquelle la fonction va chercher la pattern à nettoyé
    - Return la chaine de caractère nettoyé '''
  if pd.notna(str_):
    return re.sub(aNegliger, subst, str(str_))
  else:
    return str_
  
df_result['valeur_ajoute_totale'] = df_result['valeur_ajoute_totale'].apply(apply_reg)

## Nettoyage df result all (resultat de tous les lycées professionels)

In [13]:
#nettoyage (supression) des colonnes ou toutes les valeures sont nulles
df_result_all.dropna(axis=1,how='all',inplace=True)

#nettoyage (supression) des lignes ou toutes les valeures sont nulles
df_result_all.dropna(axis=0,how='all',inplace=True)

# L'index 1393 a une valeure ajoutée de réusiite totale = "ND"
# par contre ce lycee a un taux_reussite_total = 84
# j'ai donc décidé de rempace le "ND" par 0 (neutre) pour ce lycee et pour tous les lycee qui ont
# une valeure ajoutée de réussite totale = "ND" (non définir)
df_result_all['valeur_ajoute_totale'] = df_result_all['valeur_ajoute_totale'].apply(apply_reg)

## Transform df qui contient les resultat des lycées labelisés seulement (df_result)

In [14]:
# transformer les dates en numériques pour la prochaine opération
df_result["annee_x"] = pd.to_numeric(df_result["annee_x"])
df_result["annee_y"] = pd.to_numeric(df_result["annee_y"])

# ajouter une colonne qui contient boolean (resultat après obtention label ou pas)
# True si oui, false sinon
# les resultats des lycee après l'obtention de leurs labels 
# (annee_x pour obtention label, annee_y pour passage examens de baccalauréat)
df_result["resultat_apres_label"] = (df_result["annee_y"] >= df_result["annee_x"])

# transformer la valeur ajoutée de réussites totale en numérique
df_result["valeur_ajoute_totale"] = pd.to_numeric(df_result["valeur_ajoute_totale"])

# transorm taux_reussite_attendu_total to numeric
df_result["taux_reussite_attendu_total"] = pd.to_numeric(df_result["taux_reussite_attendu_total"])


## Transform df qui contient les résultats de tous les lycées inclus sont qui sont labelisés (df_result_all)

In [15]:
# transformer les dates en numériques pour la prochaine opération
# transformer les dates en numériques pour la prochaine opération
df_result_all["annee_y"] = pd.to_numeric(df_result_all["annee_y"])

# Creer une colonne pour dire si le lycee est labelisé : True/False
df_result_all["label_true"] = (pd.notna(df_result_all["rne"]))

# ajouter une colonne qui contient boolean (resultat après obtention label ou pas)
# True si oui, false sinon
# les resultats des lycee après l'obtention de leurs labels 
# (annee_x pour obtention label, annee_y pour passage examens de baccalauréat)
df_result_all["resultat_apres_label"] = (df_result_all["annee_y"] >= df_result_all["annee_x"]) & (df_result_all["label_true"] == True)

# remplacer tous les labels à 0 where examen passé avant 2017
df_result_all.loc[df_result_all["resultat_apres_label"] == False, "label"] = 0

# transformer la valeur ajoutée de réussites totale en numérique
df_result_all["valeur_ajoute_totale"] = pd.to_numeric(df_result_all["valeur_ajoute_totale"])

# transorm taux_reussite_attendu_total to numeric
df_result_all["taux_reussite_attendu_total"] = pd.to_numeric(df_result_all["taux_reussite_attendu_total"])

## Infos

In [16]:
df_result.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 7971 entries, 0 to 7970
Data columns (total 16 columns):
 #   Column                       Non-Null Count  Dtype  
---  ------                       --------------  -----  
 0   label                        7971 non-null   int64  
 1   annee_x                      7971 non-null   int64  
 2   localite                     7971 non-null   object 
 3   departement_x                7971 non-null   object 
 4   nom_etablissement            7971 non-null   object 
 5   position                     7971 non-null   object 
 6   rne                          7971 non-null   object 
 7   latitude                     7971 non-null   float64
 8   longitude                    7971 non-null   float64
 9   UAI                          7971 non-null   object 
 10  taux_reussite_total          7971 non-null   int64  
 11  valeur_ajoute_totale         7971 non-null   int64  
 12  taux_reussite_attendu_total  6259 non-null   float64
 13  annee_y           

# Transform for visualisations

In [17]:
# re transform annee to str so it can be a discrete value for visualisations (discrete value)
df_result["annee_x"] = df_result["annee_x"].apply(str)
df_result["annee_y"] = df_result["annee_y"].apply(str)

df_result_all["annee_x"] = df_result_all["annee_x"].apply(str)
df_result_all["annee_y"] = df_result_all["annee_y"].apply(str)

# Visualisation 

In [18]:
# Import necessary libraries
import matplotlib.pyplot as plt
import seaborn as sns
import plotly.express as px
import folium # for maps
import plotly.graph_objects as go

## Analyse général

### La proportions des Lycées labelisés et non labelisés parmis les lycées d'occitanie

In [58]:
nbre_lycee_all = df_result_all['UAI'].nunique()
nbre_lycee_all_labelise = df_result_all['rne'].nunique()
nbre_lycee_all_non_labelise = nbre_lycee_all - nbre_lycee_all_labelise
values = [nbre_lycee_all_non_labelise,nbre_lycee_all_labelise]
labels = ["Nombre de lycées non labelisés pour lesquelles on connait le resultat", "Nombre de lycées labelisés pour lesquelles on connait le resultat"]

#plot figure
fig = go.Figure(data=[go.Pie(labels=labels, values=values, title = "La proportions des Lycées labelisés parmis les lycées d'occitanie")])
fig.show()

### La proportions des Lycées mixtes et non mixtes

In [59]:
# les lycées mixtes 
df_lycee_mixte = pd.merge(df_lycee_gen, df_lycee_pro, left_on="UAI", right_on="UAI",how="inner")

#calcul des proportions
nbre_lycee_all = df_lycee_all["UAI"].nunique()
nbre_lycee_mixte = df_lycee_mixte["UAI"].nunique()
nbre_lycee_non_mixte = nbre_lycee_all - nbre_lycee_mixte

#camamber data parameters
labels = ['lycées mixtes', 'lycées non mixtes']
values = [nbre_lycee_mixte,nbre_lycee_non_mixte]

#plot figure
fig = go.Figure(data=[go.Pie(labels=labels, values=values, title = "La proportions des Lycées mixtes et non mixtes")])
fig.show()

### La proportions des Lycées mixtes, professionels non mixtes et d'enseignement générales et technologiques non mixtes

In [60]:
#calcul du nombre des lycées profess non mixtes
nbre_lycee_pro_mixte_inclus = df_lycee_pro['UAI'].nunique()
nbre_lycee_pro_uniques = nbre_lycee_pro_mixte_inclus - nbre_lycee_mixte
#calcul du nombre des lycées générales non mixtes
nbre_lycee_gen_mixte_inclus = df_lycee_gen["UAI"].nunique()
nbre_lycee_gen_uniques = nbre_lycee_gen_mixte_inclus - nbre_lycee_mixte

#data parameters for plotting camamber
labels=["Nombre de lycées d'enseignement générales et technologiques","Nombre de lycées professionels",
    "Nombre de lycées mixtes"]
values=[nbre_lycee_gen_uniques,nbre_lycee_pro_uniques,nbre_lycee_mixte]

#plot figure
fig = go.Figure(data=[go.Pie(labels=labels, values=values, title = "La proportions des Lycées mixtes, professionels et d'enseignement générales et technologiques")])
fig.show()

In [61]:
# La variation du nombre des lycées labelisés selon les années
df_proportion_lycee_labelise_annee = df_result.groupby("annee_x")["rne"].nunique()
df_proportion_lycee_labelise_annee = df_proportion_lycee_labelise_annee.reset_index()

#plotting a histogram 
fig = px.histogram(df_proportion_lycee_labelise_annee, x="annee_x", y="rne",
          color="annee_x",
           labels={"UAI" : "nombre de lycee labelisés"})
fig.update_layout(title_text="La variation du nombre des lycées labelisés selon les années")
fig.show()

**le nombre de lycées professionels labelisés a augmente de 87,17 % entre 2017 et 2021**

In [24]:
# La variation du nombre des lycées non labelisés selon les années
df_proportion_lycee_non_labelise_annee = df_result_all.query("label_true == False").groupby("annee_y")["UAI"].nunique()
df_proportion_lycee_non_labelise_annee = df_proportion_lycee_non_labelise_annee.reset_index()

#plotting a histogram 
fig = px.histogram(df_proportion_lycee_non_labelise_annee, x="annee_y", y="UAI",
          color="annee_y",
           labels={"UAI" : "nombre de lycee non labelisés"})
fig.update_layout(title_text="La variation du nombre des lycées non labelisés selon les années")
fig.show()

**Le nombre de lycées professionels non labelisés a diminué de 7.14% entre 2012 et 2021**

In [25]:
# La variation du nombre des lycées professionels (labelisé ou non) selon les années
df_lycee_pro["annee"] = df_lycee_pro["annee"].apply(str)
df_proportion_lycee_tout_annee = df_lycee_pro.groupby("annee")["UAI"].nunique()
df_proportion_lycee_tout_annee = df_proportion_lycee_tout_annee.reset_index()
df_proportion_lycee_tout_annee

#plotting a histogram 
fig = px.histogram(df_proportion_lycee_tout_annee, x="annee", y="UAI",
          color="annee",
           labels={"UAI" : "nombre de lycee non labelisés"})
fig.update_layout(title_text="La variation du nombre des lycées professionels (labelisés et non labelisés) selon les années")
fig.show()

**Le nombre des lycées professionels (labelisés et non labelisé) a augmenté de 11.39% entre 2012 et 2021**

### Conclusion

**Au fil des années, les lycées non labelisés diminuent et obtiennent des labels et deviennent alors labelisés.
De ce fait le nombre des lycées labelisés augmentent.**
**Cependant, l'augmentation du nombre des lycées professionels labelisés (87,17%) entre 2017 et 2021, n'est pas seulement expliqué par la diminution du nombre des lycées non labelisés (7,14%) entre 2012 et 2021.
Cette augmentation est aussi du au fait que des nouveaux lycées labelisés sont introduits chaque année**

## Analyse du taux de réussite des élèves dans les lycées

**Taux de réussite constaté**

- Le taux de réussite au baccalauréat est la proportion, parmi les élèves présents à l’examen, de ceux qui ont obtenu le diplôme
- Le graphique ci-dessous montre que le moyenne du taux de réussite est presque similaire selon que l'école
  a un abel 1 ou 3.
- Il est donc intéréssant d'aller voir qu'elle étaient les moyennes de taux de réussite de ces écoles avant
  obtention de leurs labels numérique !

In [62]:
# transform label to numeric
df_result["label"] = pd.to_numeric(df_result["label"])
#sort label by ascending order
df_result.sort_values(by="label",inplace=True)
# re transform label to str so it can be a discrete value for visualisations (discrete value)
df_result["label"] = df_result["label"].apply(str)

#plotting a histogram
fig = px.histogram(df_result[df_result["resultat_apres_label"] == True], x="label", y="taux_reussite_total", nbins=10, histfunc="avg", color="label")
fig.update_layout(title_text="La moyenne des taux de réussites des lycee après obtention de leurs labels  selon les labels")
fig.show()

### A NOTER LABEL 0 = PAS DE LABEL

In [63]:
# transform label to numeric
df_result_all["label"] = pd.to_numeric(df_result_all["label"])
#sort label by ascending order
df_result_all.sort_values(by="label",inplace=True)
# re transform label to str so it can be a discrete value for visualisations (discrete value)
df_result_all["label"] = df_result_all["label"].apply(str)

#plotting a histogram
fig = px.histogram(df_result_all, x="label", y="taux_reussite_total", nbins=10, histfunc="avg", color="label")
fig.update_layout(title_text="La moyenne des taux de réussites des lycee sans (label 0) et avec des labels  selon les labels")
fig.show()

**Comparaison de la moyenne du taux de réussite constaté avant et après obtention des labels numériques**

- Le graphique ci-dessous montre une amélioration des taux de réussite des écoles après obtention de leurs labels
  numérique !
- IL est donc intéréssant d'aller chercher pourquoi ? est ce que l'école a apporté plus de valeur pour les 
  élèves grace au numérique ?

In [64]:
#plotting a histogram 
fig = px.histogram(df_result, x="departement_y", y="taux_reussite_total", nbins=10,
            histfunc="avg", color="departement_y",
            facet_row="resultat_apres_label",
           labels={"taux_reussite_total" : "taux de réussite"})
fig.update_layout(title_text="La moyenne des taux de réussites totales selon les départements - avant et après obtention labels")
fig.show()

### La moyenne des taux de réussites totales avant et après obtention labels

In [65]:
#plotting a histogram 
fig = px.histogram(df_result, x="resultat_apres_label", y="taux_reussite_total", nbins=10,
            histfunc="avg", color="resultat_apres_label",
           labels={"taux_reussite_total" : "taux de réussite"})
fig.update_layout(title_text="La moyenne des taux de réussites totales avant et après obtention labels")
fig.show()

In [66]:
#plotting a histogram 
fig = px.histogram(df_result, x="rne", y="taux_reussite_total", nbins=10, histfunc="avg", color="departement_y", facet_row="resultat_apres_label",
         labels={"taux_reussite_total" : "taux de réussite"})
fig.update_layout(title_text="La moyenne des taux de réussites de chaque lycée  avant et après obtention labels")
fig.show()

**Pourquoi certains lycées n'apparaissent pas dans le resultat après labels malgré qu'ils ont des labels ?**
- simplement parce ces lycées n'ont pas eu de passages d'examens après obtentions de labels

### On va voir la différence des résultats entre les lycées labelisés et ceux qui ne le sont pas

In [69]:
#plotting a histogram 
fig = px.histogram(df_result_all, x="resultat_apres_label", y="taux_reussite_total", nbins=10,
            histfunc="avg", color="resultat_apres_label",
           labels={"taux_reussite_total" : "taux de réussite"})
fig.update_layout(title_text="La moyenne des taux de réussites sans et avec labels")
fig.show()

In [70]:
#plotting a bocplot 
fig = px.box(df_result_all, x="resultat_apres_label", y="taux_reussite_total",
       color="resultat_apres_label",
      labels={"taux_reussite_total" : "taux de réussite"})
fig.update_layout(title_text="La variance des taux de réussites sans et avec labels")
fig.show()

In [71]:
# transform label to numeric
df_result_all["annee_y"] = pd.to_numeric(df_result_all["annee_y"])
#sort label by ascending order
df_result_all.sort_values(by="annee_y",inplace=True)
# re transform label to str so it can be a discrete value for visualisations (discrete value)
df_result_all["annee_y"] = df_result_all["annee_y"].apply(str)

#plotting a bocplot 
fig = px.box(df_result_all, x="annee_y", y="taux_reussite_total",
       color="resultat_apres_label",
      labels={"taux_reussite_total" : "taux de réussite"})
fig.update_layout(title_text="La moyenne des taux de réussites sans et avec labels par année")
fig.show()

**On constate que les lycées professionels labelisés ont un meilleur résultat que ceux non labelisés (toutes années confondues)**
 - On se demande pourquoi ?
 - On sait que parmis les lycées professionels, 33% ne sont pas labelisés, et 67% sont labelisés.
 - Alors nous souhaitons répondre à la question suivante : y'a t'il un effet de la labélisation sur le taux de réussite des lycées professionels ?
 - Pour cela on pose les hypothèses suivantes : 
   - H0 : La labélisation d'un lycee professionel n'a pas d'effet sur son taux de réussite 
   - H1 : La labélisation d'un lycee professionel a un effet sur son taux de réussite 

### Covid
**Nous constatons un pic de taux de réussite des lycées en 2020, puis une diminution de ce taux en 2021**

## Analyse de la valeur ajoutée de réussite 
- la valeur ajoutée de l’établissement est la différence entre le taux constaté de l’établissement et le taux attendu. 

  **Valeur ajoutée = taux constaté – taux attendu**
  

- Le graphique ci-dessous montre une moyenne de valeur ajoutée de label 3 plus petite que label 1.
  C'est étonnant, mais est-ce que ça veut dire que les écoles ayant un label 3 ont contribué moins
  à la réussite des élèves ?.
- En effet, peut etre que les écoles ayant un label 3, ont un taux de réussite attendu beaucoup plus elevé 
  que les écoles avec un label plus faible. De ce fait, l'augmentation du taux de réussite attendu 
  peut diminuer la valeur ajoutée de l'école.

In [73]:
# transform label to numeric
df_result_all["label"] = pd.to_numeric(df_result_all["label"])
#sort label by ascending order
df_result_all.sort_values(by="label",inplace=True)
# re transform label to str so it can be a discrete value for visualisations (discrete value)
df_result_all["label"] = df_result_all["label"].apply(str)

#plotting a histogram 
fig = px.histogram(df_result_all, x="label", y="valeur_ajoute_totale", nbins=10, histfunc="avg", color="label")
fig.update_layout(title_text="La moyenne des valeurs ajoutées de réussites  selon les labels")
fig.show()

**Comparaison des valeurs ajoutées des écoles avant et après obtention des labels numériques**

- le graphique ci-dessous montre une véritables amélioration des valeurs ajoutée des écoles après obtention de labels. Surtout pour le département de LOZERE pour lequel la valeur ajoutée est passée du **-** à **+** !

In [74]:
#plotting a histogram 
fig = px.histogram(df_result, x="departement_y", y="valeur_ajoute_totale", nbins=10, histfunc="avg", color="departement_y", facet_row="resultat_apres_label")
fig.update_layout(title_text="La moyenne des valeurs ajoutés de réussites  selon les départements avant et après obtention labels")
fig.show()

In [75]:
#plotting a histogram 
fig = px.histogram(df_result, x="resultat_apres_label", y="valeur_ajoute_totale", nbins=10, histfunc="avg", color="resultat_apres_label")
fig.update_layout(title_text="La moyenne des valeurs ajoutés de réussites  avant et après obtention labels")
fig.show()

### Comparaison de la moyenne des valeurs ajoutés de réussites des lycées sans et avec labels

In [77]:
#plotting a histogram 
fig = px.histogram(df_result_all, x="resultat_apres_label", y="valeur_ajoute_totale", nbins=10, histfunc="avg", color="resultat_apres_label")
fig.update_layout(title_text="La moyenne des valeurs ajoutés de réussites sans et avec labels")
fig.show()

In [78]:
#plotting a bocplot 
fig = px.box(df_result_all, x="resultat_apres_label", y="valeur_ajoute_totale",
       color="resultat_apres_label",
      labels={"valeur_ajoute_totale" : "taux de valeur ajoutée "})
fig.update_layout(title_text="La variance des taux de réussites sans et avec labels")
fig.show()

In [79]:
# transform label to numeric
df_result_all["annee_y"] = pd.to_numeric(df_result_all["annee_y"])
#sort label by ascending order
df_result_all.sort_values(by="annee_y",inplace=True)
# re transform label to str so it can be a discrete value for visualisations (discrete value)
df_result_all["annee_y"] = df_result_all["annee_y"].apply(str)

#plotting a bocplot 
fig = px.box(df_result_all, x="annee_y", y="valeur_ajoute_totale",
       color="resultat_apres_label",
      labels={"valeur_ajoute_totale" : "taux de valeur ajoutée "})
fig.update_layout(title_text="La variance des taux de réussites sans et avec labels par année")
fig.show()

## Analyse du taux de réussite attendu en france

In [81]:
# transform label to numeric
df_result_all["label"] = pd.to_numeric(df_result_all["label"])
#sort label by ascending order
df_result_all.sort_values(by="label",inplace=True)
# re transform label to str so it can be a discrete value for visualisations (discrete value)
df_result_all["label"] = df_result_all["label"].apply(str)

#plotting a histogram 
fig = px.histogram(df_result_all, x="label", y="taux_reussite_attendu_total", nbins=10, histfunc="avg", color="label")
fig.update_layout(title_text="La moyenne des taux de réussite attendu en france selon les labels")
fig.show()

### Comparaison du taux de réussite des élèves des lycées avant et après obtention des labels

In [80]:
#plotting a histogram 
fig = px.histogram(df_result, x="departement_y", y="taux_reussite_attendu_total", nbins=10,
            histfunc="avg", color="departement_y",
            facet_row="resultat_apres_label",
           labels={"taux_reussite_attendu_total" : "Taux_réussite_attendu"})
fig.update_layout(title_text="La moyenne des taux de réussite attendu en france  selon les départements - avant et après obtention labels")
fig.show()

In [83]:
#plotting a histogram 
fig = px.histogram(df_result, x="resultat_apres_label", y="taux_reussite_attendu_total", nbins=10,
            histfunc="avg", color="resultat_apres_label",
           labels={"taux_reussite_attendu_total" : "Taux_réussite_attendu"})
fig.update_layout(title_text="La moyenne des taux de réussite attendu en france avant et après obtention labels")
fig.show()

### Comparaison du taux de réussite des élèces aux lycées professionels attendu en france  sans et avec labels

In [84]:
#plotting a histogram 
fig = px.histogram(df_result_all, x="resultat_apres_label", y="taux_reussite_attendu_total", nbins=10,
            histfunc="avg", color="resultat_apres_label",
           labels={"taux_reussite_attendu_total" : "Taux_réussite_attendu"})
fig.update_layout(title_text="La moyenne des taux de réussite attendu en france sans et avec labels")
fig.show()

## Analyse temporelles

In [85]:
# transform label to numeric
df_result_all["annee_y"] = pd.to_numeric(df_result_all["annee_y"])
#sort label by ascending order
df_result_all.sort_values(by="annee_y",inplace=True)
# re transform label to str so it can be a discrete value for visualisations (discrete value)
df_result_all["annee_y"] = df_result_all["annee_y"].apply(str)

fig = px.scatter(df_result_all,
         x = "annee_y",
         y = "taux_reussite_total",
         color = "UAI",
         hover_name="taux_reussite_total",
       hover_data=["label"],
       title = "Le taux de réussite des lycées professionels non labeisés en 2012 en fonction des années")

plt.tight_layout()
fig.show()

<Figure size 432x288 with 0 Axes>

# ANOVA 

## Effet de la labélisation sur le taux de réussite des lycées

In [86]:
import statsmodels.api as sa
import statsmodels.formula.api as sfa
import scikit_posthocs as sp
from statsmodels.stats.multicomp import pairwise_tukeyhsd
import scipy.stats as stats

### Résultat de l'anova

In [87]:
lm = sfa.ols('taux_reussite_total ~ C(label)', data=df_result_all).fit()
anova = sa.stats.anova_lm(lm)
anova

df         sum_sq      mean_sq          F        PR(>F)
C(label)     3.0    8696.448132  2898.816044  39.609113  2.017794e-25
Residual  9063.0  663280.943728    73.185584        NaN           NaN

### Analyse de l'anova

**P_value < alpha (0,05), donc on rejette H0 et on conclut d'une manière significative un effet du label numérique sur le taux de réussite des lycées**

### Test de Tukey
 - permet de préciser quelles modalités de la variable qualitative label a provoqué ce rejet

In [88]:
# perform Tukey's test
tukey = pairwise_tukeyhsd(endog=df_result_all['taux_reussite_total'],
             groups=df_result_all['label'],
             alpha=0.05)

#display results
print(tukey)

Multiple Comparison of Means - Tukey HSD, FWER=0.05
group1 group2 meandiff p-adj   lower  upper  reject
---------------------------------------------------
   0.0    1.0   2.1142   -0.0  1.5269 2.7014   True
   0.0    2.0   2.3554    0.0   1.355 3.3558   True
   0.0    3.0   2.4795 0.0007  0.8234 4.1357   True
   1.0    2.0   0.2412 0.9421 -0.8537 1.3362  False
   1.0    3.0   0.3654 0.9473 -1.3496 2.0803  False
   2.0    3.0   0.1241 0.9983 -1.7724 2.0207  False
---------------------------------------------------


### Analyse de test de tukey 
**Le test de tukey est utilisé pour comparer les moyennes de plusieurs groupes. Le test est utilisé pour déterminer s'il existe des différences significatives entre les moyennes de différents groupes.
L'output montre les résultats du test pour chaque comparaison à paires de groupes. Les colonnes de l'output incluent:**
- group1 et group2: les groupes étant comparés
- meandiff: la différence des moyennes entre les deux groupes
- p-adj: la valeur p ajustée pour la comparaison
- lower et upper: les limites inférieure et supérieure de l'intervalle de confiance de 95% pour la différence des moyennes
- reject: si oui ou non l'hypothèse nulle (que les moyennes sont égales) peut être rejetée en fonction de la valeur p et du niveau alpha choisi (0,05 dans ce cas)

**Ce test compare les moyennes de quatre groupes: 0.0, 1.0, 2.0 et 3.0.**
- Pour le groupe 0.0 et 1.0, la valeur p-adj est de 0.0, ce qui indique que la différence de moyenne est statistiquement significative au niveau de 0.05.
- Pour le groupe 0.0 et 2.0, la valeur p-adj est de 0.0, ce qui indique que la différence de moyenne est statistiquement significative au niveau de 0.05.
- Pour le groupe 1.0 et 3.0, la valeur p-adj est de 0.0, ce qui indique que la différence de moyenne est statistiquement significative au niveau de 0.05

### Shapiro test : Tester l'hypothèse de normalité
 - H0 : Les échatillons sont gaussiens

In [89]:
# Split the data
x = df_result_all.groupby('label')['taux_reussite_total'].apply(list)

In [90]:
# Perform Shapiro-Wilk test
stat, p = stats.shapiro(x[0])
print("Shapiro-Wilk test: statistic=%f, p-value=%f" % (stat, p))
if p > 0.05:
  print("The data is likely normal")
else:
  print("The data is likely not normal")

Shapiro-Wilk test: statistic=0.937840, p-value=0.000000
The data is likely not normal


/home/ubuntu/anaconda3/lib/python3.9/site-packages/scipy/stats/morestats.py:1760: UserWarning:

p-value may not be accurate for N > 5000.



**p value < 0.05 donc on rejette H0 et on conclut que les échantillons ne sont plutot pas gaussiens**

### Levene's test : Tester l'hypothèse d'homoscédasticité
- H0 : Les variances sont égales

**L'hyphothèse de normalité n'est pas validé, donc on réalise un test de Levene pour tester l'hypothèse d'homoscédasticité**

In [91]:
# Perform Levene's test
stat, p = stats.levene(x[0], x[1], x[2], x[3])
print("Levene's test: statistic=%.3f, p-value=%.3f" % (stat, p))
if p > 0.05:
  print("The variances of the samples are likely similar")
else:
  print("The variances of the samples are likely different")

Levene's test: statistic=5.533, p-value=0.001
The variances of the samples are likely different


**p value < 0,05 donc on rejette H0 et on conclut que les variances des labels ne sont plutot pas égales**

## Effet de la labélisation sur le taux de réussite deslycées
### Résultat de l'anova

In [92]:
lm = sfa.ols('valeur_ajoute_totale ~ C(label)', data=df_result_all).fit()
anova = sa.stats.anova_lm(lm)
anova

df         sum_sq    mean_sq         F    PR(>F)
C(label)     3.0     250.824958  83.608319  2.965451  0.030755
Residual  9063.0  255523.445474  28.194135       NaN       NaN

### Analyse de l'anova

**P_value < alpha (0,05), donc on rejette H0 et on conclut d'une manière significative un effet du label numérique sur la valeur ajoutée de réussite deslycées**

### Test de Tukey

In [93]:
# perform Tukey's test
tukey = pairwise_tukeyhsd(endog=df_result_all['valeur_ajoute_totale'],
             groups=df_result_all['label'],
             alpha=0.05)

#display results
print(tukey)

Multiple Comparison of Means - Tukey HSD, FWER=0.05 
group1 group2 meandiff p-adj   lower   upper  reject
----------------------------------------------------
   0.0    1.0   0.1134 0.8547 -0.2511  0.4779  False
   0.0    2.0   0.0378 0.9986 -0.5831  0.6587  False
   0.0    3.0  -1.1205 0.0263 -2.1484 -0.0925   True
   1.0    2.0  -0.0756 0.9919 -0.7552   0.604  False
   1.0    3.0  -1.2339 0.0154 -2.2983 -0.1694   True
   2.0    3.0  -1.1583 0.0557 -2.3354  0.0189  False
----------------------------------------------------


### Analyse de test de tukey 

**Ce test compare les moyennes de quatre groupes: 0.0, 1.0, 2.0 et 3.0.**
- Pour le groupe 0.0 et 3.0, la valeur p-adj est de 0.02, ce qui indique que la différence de moyenne est statistiquement significative au niveau de 0.05.
- Pour le groupe 1.0 et 3.0, la valeur p-adj est de 0.01, ce qui indique que la différence de moyenne est statistiquement significative au niveau de 0.05

### Shapiro test : Tester l'hypothèse de normalité
 - H0 : Les échatillons sont gaussiens

In [94]:
# Split the data
x = df_result_all.groupby('label')['valeur_ajoute_totale'].apply(list)

In [95]:
# Perform Shapiro-Wilk test
stat, p = stats.shapiro(x[0])
print("Shapiro-Wilk test: statistic=%f, p-value=%f" % (stat, p))
if p > 0.05:
  print("The data is likely normal")
else:
  print("The data is likely not normal")

Shapiro-Wilk test: statistic=0.972493, p-value=0.000000
The data is likely not normal


/home/ubuntu/anaconda3/lib/python3.9/site-packages/scipy/stats/morestats.py:1760: UserWarning:

p-value may not be accurate for N > 5000.



### Levene's test : Tester l'hypothèse d'homoscédasticité
- H0 : Les variances sont égales

In [96]:
# Perform Levene's test
stat, p = stats.levene(x[0], x[1], x[2], x[3])
print("Levene's test: statistic=%.3f, p-value=%.3f" % (stat, p))
if p > 0.05:
  print("The variances of the samples are likely similar")
else:
  print("The variances of the samples are likely different")

Levene's test: statistic=32.003, p-value=0.000
The variances of the samples are likely different
